## SDK code to create CUSTOMER_Time_Since_Latest_Change_in_PostalCode

Feature description:
>Time (in days) Since Latest Change in PostalCode for the customer.

In [ ]:
import featurebyte as fb
fb.use_profile("tutorial")

### Activate catalog

 See [SDK reference for catalogs](https://docs.featurebyte.com/latest/reference/core/catalog/)

In [ ]:
catalog = fb.Catalog.activate("Grocery Dataset Tutorial")

### Get view from table
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Get view from GROCERYCUSTOMER scd table.
grocerycustomer_view = catalog.get_view("GROCERYCUSTOMER")

### Create features on changes in GROCERYCUSTOMER PostalCode

In [ ]:
# Create change view from GROCERYCUSTOMER table to track changes in PostalCode.
grocerycustomer_postalcode_change_view =\
catalog.get_table("GROCERYCUSTOMER").get_change_view(
    track_changes_column = "PostalCode"
)

In [ ]:
# Filter view to remove change records that correspond to first setting of the field.
cond = grocerycustomer_postalcode_change_view.past_PostalCode.isnull()
grocerycustomer_postalcode_change_view =\
grocerycustomer_postalcode_change_view[~cond]

In [ ]:
# Group grocerycustomer_postalcode_change_view view by customer entity (GroceryCustomerGuid).
grocerycustomer_postalcode_change_view_by_customer =\
grocerycustomer_postalcode_change_view.groupby("GroceryCustomerGuid")

In [ ]:
# Get Latest Change in PostalCode for the customer.
customer_latest_change_in_postalcode =\
grocerycustomer_postalcode_change_view_by_customer.aggregate_over(
    "new_ValidFrom", method="latest",
    feature_names=["customer_Latest_Change_in_PostalCode"],
    windows=[None]
)["customer_Latest_Change_in_PostalCode"]

In [ ]:
# Compare customer_Latest_Change_in_PostalCode with point-in-time in days
customer_time_since_latest_change_in_postalcode = (
    fb.RequestColumn.point_in_time()
    - customer_latest_change_in_postalcode
).dt.day
# Give a name to new feature
customer_time_since_latest_change_in_postalcode.name = \
"CUSTOMER_Time_Since_Latest_Change_in_PostalCode"

### Preview feature
 Read on [the feature primary entity concept](https://docs.featurebyte.com/latest/about/glossary/#feature-primary-entity)

 Read on [the serving entity concept](https://docs.featurebyte.com/latest/about/glossary/#serving-entity)

 See [SDK reference for observation table](https://docs.featurebyte.com/latest/reference/core/observation_table/)

 See [SDK reference to preview feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)

In [ ]:
#Check the primary entity of the feature'
customer_time_since_latest_change_in_postalcode.primary_entity

In [ ]:
#Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table(
	"Preview Table with 10 Customers"
).to_pandas()

In [ ]:
#Preview CUSTOMER_Time_Since_Latest_Change_in_PostalCode
customer_time_since_latest_change_in_postalcode.preview(
	preview_table
)

### Save feature
 See [SDK reference to save feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)

In [ ]:
# Save feature
customer_time_since_latest_change_in_postalcode.save()

### Add description and see feature definition file
 See [SDK reference for the definition file of a feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)

In [ ]:
# Add description
customer_time_since_latest_change_in_postalcode.update_description(
	"Time (in days) Since Latest Change in PostalCode for the customer."
)
# See feature definition file
customer_time_since_latest_change_in_postalcode.definition